 ### 1. 서울시 공공데이터 제공 장소 116곳 리스트 뽑기


In [402]:
##### API 가져와보기
import requests
import pandas as pd 
import json
from urllib.parse import quote
from bs4 import BeautifulSoup

# 서울 지역 116곳 번호 뽑기
area_list = []
try:
    for i in range(1,63):
        area = f"POI{i:03d}"

        # API 키
        api_key = '6e51654f776b353335387168745664'
        # API URL 구성
        url = f'http://openapi.seoul.go.kr:8088/{api_key}/xml/citydata/1/1000/{area}'
        # API 요청, 응답
        response = requests.get(url)
        xml_data = response.text
        # xml파싱
        soup = BeautifulSoup(xml_data, 'lxml-xml')
        area_name = soup.find('AREA_NM').text 
        address = soup.find('ROAD_ADDR')
        print(soup)
        print(area_name)

except :
    # 오류 발생 시 실행되는 코드
    print("오류가 발생했습니다.")

<?xml version="1.0" encoding="utf-8"?>
<SeoulRtd.citydata><list_total_count>1</list_total_count><RESULT><RESULT.CODE>INFO-000</RESULT.CODE><RESULT.MESSAGE>정상 처리되었습니다.</RESULT.MESSAGE></RESULT><CITYDATA><AREA_NM>강남 MICE 관광특구</AREA_NM><AREA_CD>POI001</AREA_CD><LIVE_PPLTN_STTS><LIVE_PPLTN_STTS><AREA_NM>강남 MICE 관광특구</AREA_NM><AREA_CD>POI001</AREA_CD><AREA_CONGEST_LVL>약간 붐빔</AREA_CONGEST_LVL><AREA_CONGEST_MSG>사람들이 몰려있을 가능성이 크고 붐빈다고 느낄 수 있어요. 인구밀도가 높은 구간에서는 도보 이동시 부딪힘이 발생할 수 있어요.</AREA_CONGEST_MSG><AREA_PPLTN_MIN>22000</AREA_PPLTN_MIN><AREA_PPLTN_MAX>24000</AREA_PPLTN_MAX><MALE_PPLTN_RATE>48.2</MALE_PPLTN_RATE><FEMALE_PPLTN_RATE>51.8</FEMALE_PPLTN_RATE><PPLTN_RATE_0>0.0</PPLTN_RATE_0><PPLTN_RATE_10>1.8</PPLTN_RATE_10><PPLTN_RATE_20>23.4</PPLTN_RATE_20><PPLTN_RATE_30>33.3</PPLTN_RATE_30><PPLTN_RATE_40>23.2</PPLTN_RATE_40><PPLTN_RATE_50>12.7</PPLTN_RATE_50><PPLTN_RATE_60>4.2</PPLTN_RATE_60><PPLTN_RATE_70>1.3</PPLTN_RATE_70><RESNT_PPLTN_RATE>37.8</RESNT_PPLTN_RATE><NON_RESNT_PPLTN_RATE>62.2</NO

### 2. 가져온 지역 한개에서 요소 가져오기 

In [404]:
# 특정 요소 내의 모든 항목 찾기
live_ppltn = soup.find('LIVE_PPLTN_STTS')
#지역
area_nm = live_ppltn.find('AREA_NM').text
#혼잡도
congestion = live_ppltn.find('AREA_CONGEST_LVL').text
print(f"지역: {area_nm}, 혼잡도: {congestion}")
#자치구 
address = soup.find('ADDRESS').text
print(address)


지역: 낙산공원·이화마을, 혼잡도: 여유


AttributeError: 'NoneType' object has no attribute 'text'

#### 2.1데이터분석에 필요한 값들이 잘나오는지 하나씩 확인해보자

In [ ]:

## 서울시 실시간 데이터 가져오기

#데이트 날씨 점수 = 강수점수(30) + 기온점수(20) + 대기질점수(15) + 하늘상태점수(15) 

#### 가져올 값
#핫스팟 장소명(LIVE_PPLTN_STTS), 

#### 날씨 정보
#기온(TEMP), 강수(PRECIPITATION),강수확률(RAIN_CHANCE), 강수형태(PRECPT_TYPE), 대기질(AIR_IDX), 하늘상태(SKY_STTS), 습도(HUMIDITY), 자외선(UV_INDEX)

#### 혼잡도 정보
#장소 혼잡도 지표(AREA_CONGEST_LVL), 실시간 상권현황 (LIVE_CMRCL_STTS),  장소 예측 혼잡도 지표 (FCST_CONGEST_LVL), 장소 실시간 상권 현황(AREA_CMRCL_LVL)

##불쾌지수 = 1.8 x 기온 – 0.55 x (1 – 습도) x (1.8 x 기온 – 26) + 32

In [406]:
rain_mm =[]
# 강수량 (-일때 0으로 변경)
rain_mm_list = soup.find('PRECIPITATION')
for rain in rain_mm_list:
    rain = rain.text
    if rain == "-":
        rain_mm.append("0")
    else:
        rain_mm.append(rain)
    print(rain)
    
print(len(rain_mm))

-
1


In [ ]:
#온도
temp = soup.find_all('TEMP')
print(temp)
print(len(temp))

[<TEMP>15.2</TEMP>, <TEMP>14</TEMP>, <TEMP>13</TEMP>, <TEMP>12</TEMP>, <TEMP>10</TEMP>, <TEMP>10</TEMP>, <TEMP>9</TEMP>, <TEMP>9</TEMP>, <TEMP>9</TEMP>, <TEMP>9</TEMP>, <TEMP>9</TEMP>, <TEMP>8</TEMP>, <TEMP>8</TEMP>, <TEMP>8</TEMP>, <TEMP>9</TEMP>, <TEMP>10</TEMP>, <TEMP>12</TEMP>, <TEMP>14</TEMP>, <TEMP>17</TEMP>, <TEMP>19</TEMP>, <TEMP>20</TEMP>, <TEMP>17</TEMP>, <TEMP>16</TEMP>, <TEMP>14</TEMP>, <TEMP>13</TEMP>]
25


In [ ]:
#강수확률
rain_pct = soup.find_all('RAIN_CHANCE') 
print(rain_pct)
print(len(rain_pct))

[<RAIN_CHANCE>0</RAIN_CHANCE>, <RAIN_CHANCE>0</RAIN_CHANCE>, <RAIN_CHANCE>0</RAIN_CHANCE>, <RAIN_CHANCE>0</RAIN_CHANCE>, <RAIN_CHANCE>0</RAIN_CHANCE>, <RAIN_CHANCE>0</RAIN_CHANCE>, <RAIN_CHANCE>0</RAIN_CHANCE>, <RAIN_CHANCE>20</RAIN_CHANCE>, <RAIN_CHANCE>30</RAIN_CHANCE>, <RAIN_CHANCE>20</RAIN_CHANCE>, <RAIN_CHANCE>0</RAIN_CHANCE>, <RAIN_CHANCE>0</RAIN_CHANCE>, <RAIN_CHANCE>30</RAIN_CHANCE>, <RAIN_CHANCE>30</RAIN_CHANCE>, <RAIN_CHANCE>20</RAIN_CHANCE>, <RAIN_CHANCE>20</RAIN_CHANCE>, <RAIN_CHANCE>30</RAIN_CHANCE>, <RAIN_CHANCE>20</RAIN_CHANCE>, <RAIN_CHANCE>20</RAIN_CHANCE>, <RAIN_CHANCE>30</RAIN_CHANCE>, <RAIN_CHANCE>20</RAIN_CHANCE>, <RAIN_CHANCE>0</RAIN_CHANCE>, <RAIN_CHANCE>0</RAIN_CHANCE>, <RAIN_CHANCE>20</RAIN_CHANCE>]
24


In [ ]:
#강수형태
rain_type = soup.find_all('PRECPT_TYPE') # 없음 출력
print(rain_type)
print(len(rain_type))

[<PRECPT_TYPE>없음</PRECPT_TYPE>, <PRECPT_TYPE>없음</PRECPT_TYPE>, <PRECPT_TYPE>없음</PRECPT_TYPE>, <PRECPT_TYPE>없음</PRECPT_TYPE>, <PRECPT_TYPE>없음</PRECPT_TYPE>, <PRECPT_TYPE>없음</PRECPT_TYPE>, <PRECPT_TYPE>없음</PRECPT_TYPE>, <PRECPT_TYPE>없음</PRECPT_TYPE>, <PRECPT_TYPE>없음</PRECPT_TYPE>, <PRECPT_TYPE>없음</PRECPT_TYPE>, <PRECPT_TYPE>없음</PRECPT_TYPE>, <PRECPT_TYPE>없음</PRECPT_TYPE>, <PRECPT_TYPE>없음</PRECPT_TYPE>, <PRECPT_TYPE>없음</PRECPT_TYPE>, <PRECPT_TYPE>없음</PRECPT_TYPE>, <PRECPT_TYPE>없음</PRECPT_TYPE>, <PRECPT_TYPE>없음</PRECPT_TYPE>, <PRECPT_TYPE>없음</PRECPT_TYPE>, <PRECPT_TYPE>없음</PRECPT_TYPE>, <PRECPT_TYPE>없음</PRECPT_TYPE>, <PRECPT_TYPE>없음</PRECPT_TYPE>, <PRECPT_TYPE>없음</PRECPT_TYPE>, <PRECPT_TYPE>없음</PRECPT_TYPE>, <PRECPT_TYPE>없음</PRECPT_TYPE>, <PRECPT_TYPE>없음</PRECPT_TYPE>]
25


In [ ]:
#대기질
air_idx = soup.find_all('AIR_IDX') #24동안 1하나만
print(air_idx)
print(len(air_idx))

[<AIR_IDX>나쁨</AIR_IDX>]
1


In [ ]:
#하늘상태
sty_stts = soup.find_all('SKY_STTS') #24동안 1하나만
print(sty_stts)
print(len(sty_stts))

[<SKY_STTS>구름많음</SKY_STTS>, <SKY_STTS>구름많음</SKY_STTS>, <SKY_STTS>맑음</SKY_STTS>, <SKY_STTS>맑음</SKY_STTS>, <SKY_STTS>맑음</SKY_STTS>, <SKY_STTS>맑음</SKY_STTS>, <SKY_STTS>맑음</SKY_STTS>, <SKY_STTS>구름많음</SKY_STTS>, <SKY_STTS>흐림</SKY_STTS>, <SKY_STTS>구름많음</SKY_STTS>, <SKY_STTS>맑음</SKY_STTS>, <SKY_STTS>맑음</SKY_STTS>, <SKY_STTS>흐림</SKY_STTS>, <SKY_STTS>흐림</SKY_STTS>, <SKY_STTS>구름많음</SKY_STTS>, <SKY_STTS>구름많음</SKY_STTS>, <SKY_STTS>흐림</SKY_STTS>, <SKY_STTS>구름많음</SKY_STTS>, <SKY_STTS>구름많음</SKY_STTS>, <SKY_STTS>흐림</SKY_STTS>, <SKY_STTS>구름많음</SKY_STTS>, <SKY_STTS>맑음</SKY_STTS>, <SKY_STTS>맑음</SKY_STTS>, <SKY_STTS>구름많음</SKY_STTS>]
24


In [ ]:
#습도
humidity = soup.find_all('HUMIDITY') 
print(humidity)
print(len(humidity))

[<HUMIDITY>64</HUMIDITY>]
1


#### 오후 온도 구하기

In [ ]:
from collections import Counter

fcst24hours = soup.find('FCST24HOURS')  # 단일 컨테이너 요소를 찾음
fcst_items = fcst24hours.find_all('FCST_DT')  # 또는 실제 항목 태그명으로 변경
temp_list=[]
sky_status_list = []
for item in fcst_items:
    hours = item.text
   
    # 원하는 시간대 확인 (12시~18시)
    if any(time in hours for time in ['1200', '1300', '1400', '1500', '1600', '1700', '1800']):

        
        parent = item.parent
        temp = int(parent.find('TEMP').text)
        temp_list.append(temp)
        sky_status_list.append(parent.find('SKY_STTS').text) #24동안 1하나만
        print(sty_stts)
# 오후 하늘상태 구하기
counter = Counter(sky_status_list)

# 온도 평균 구하기(합/개수)
avg_temp = int(sum(temp_list) / len(temp_list))
print(avg_temp)

구름많음
구름많음
구름많음
흐림
구름많음
맑음
맑음
16


In [ ]:
# 반복해서 구해야할 온도계수


### 오후날씨 함수만들기

In [ ]:
#리스트 가져오기
def get_after_wether(value):
    from collections import Counter

    fcst24hours = soup.find('FCST24HOURS')  # 단일 컨테이너 요소를 찾음
    fcst_items = fcst24hours.find_all('FCST_DT')  # 또는 실제 항목 태그명으로 변경

    after_list =[]
    #리스트마다 행하나씩 뽑기
    for item in fcst_items:
        hours = item.text
        
        if any(time in hours for time in ['1100','1200', '1300', '1400', '1500', '1600', '1700', '1800']):
            #상위 요소로 올라가기
            parent = item.parent
            
            #value가 온도일때 온도값 주기
            if value == 'temp':
                try:
                    temp = int(parent.find('TEMP').text)
                    after_list.append(temp)
                except:
                    print("온도값에 오류가 발생")
            #하늘상태일때 하늘상태값 주기 # 맑음 문자로 나옴 카운드 ?
            elif value == 'sky_stts':
                try:
                    sky_stts = parent.find('SKY_STTS').text
                    after_list.append(sky_stts)
                    print(sky_stts)
                except:
                    print("하늘상태값에 오류가 발생")
            #강수확률일때 강수확률값주기
            elif value == 'rain_chance':
                try:
                    rain_chance = int(parent.find('RAIN_CHANCE').text)
                    
                    after_list.append(rain_chance)
                    print(rain_chance)
                except:
                    print("강수확률값에 오류가 발생")

            # 강수량일때 (-일때 0으로 변경)
            elif value == 'rain_mm':
                try:
                    rain = parent.find('PRECIPITATION').text
                    if rain == "-":
                        after_list.append(int("0"))
                    else:
                        after_list.append(int(rain))
                    print(rain)
                except:
                    #오류발생
                    print("강수량 값에 대한 오류가 발생")   

    # 리스트 평균 구하기(합/개수)
    if value in ['temp', 'rain_chance', 'rain_mm']:
        avg_after = int(sum(after_list) / len(after_list))
        return avg_after
    else:
        return Counter(after_list).most_common(1)[0][0]

           

### 인구혼잡도 함수

In [ ]:

        
def get_many_people():
    from collections import Counter
    fcst24hours = soup.find('FCST_PPLTN')  # 단일 컨테이너 요소를 찾음
    fcst_items = fcst24hours.find_all('FCST_TIME')  # 또는 실제 항목 태그명으로 변경
    after_list =[]
    #리스트마다 행하나씩 뽑기
    for item in fcst_items:
        print(item)
        hours = item.text
        print(hours)
        if any(time in hours for time in ['11:00','12:00', '13:00', '14:00', '15:00', '16:00', '17:00', '18:00']):
            try:
                parent= item.parent
                many_level=parent.find('FCST_CONGEST_LVL').text
                after_list.append(many_level)
                print(many_level)
            except:
                print("혼잡도값에 대한 오류")
    
    return Counter(after_list).most_common(1)[0][0]


In [ ]:
aaa = get_after_wether('sky_stts')
print("값 :"+ aaa)

흐림
구름많음
구름많음
흐림
구름많음
맑음
맑음
구름많음
값 :구름많음


In [ ]:
bbb = get_many_people()
print(bbb)

IndexError: list index out of range

In [ ]:
#자외선
uv_index = soup.find_all('UV_INDEX') 
print(uv_index)
print(len(uv_index))

[<UV_INDEX>낮음</UV_INDEX>]
1


#### 2.2 실시간 인구 지표값 가져오기

In [ ]:
area_name = soup.find_all('AREA_NM') 
parent = area_name.parent
area_person_many = soup.find_all('AREA_CONGEST_LVL') 
live_cmrcl_stts = soup.find_all('LIVE_CMRCL_STTS') 
fcst_person_many = soup.find_all('FCST_CONGEST_LVL') # 12시간 예측
area_cmrcl_lvl = soup.find_all('AREA_CMRCL_LVL') 

fcst_person_many = soup.find_all('FCST_CONGEST_LVL') # 12시간 예측



#핫스팟장소명
print(area_name)
print(len(area_name))
# 장소 혼잡도 지표
print(area_person_many)
print(len(area_person_many))
# 실시간 상권현황
print(live_cmrcl_stts)
print(len(live_cmrcl_stts))
# 장소 예측 혼잡도 지표 
print(fcst_person_many)
print(len(fcst_person_many))
# 장소 실시간 상권 현황
print(area_cmrcl_lvl)
print(len(area_cmrcl_lvl))

[<AREA_NM>노들섬</AREA_NM>, <AREA_NM>노들섬</AREA_NM>]
2
[<AREA_CONGEST_LVL>여유</AREA_CONGEST_LVL>]
1
[<LIVE_CMRCL_STTS/>]
1
[<FCST_CONGEST_LVL>보통</FCST_CONGEST_LVL>, <FCST_CONGEST_LVL>여유</FCST_CONGEST_LVL>, <FCST_CONGEST_LVL>여유</FCST_CONGEST_LVL>, <FCST_CONGEST_LVL>여유</FCST_CONGEST_LVL>, <FCST_CONGEST_LVL>여유</FCST_CONGEST_LVL>, <FCST_CONGEST_LVL>여유</FCST_CONGEST_LVL>, <FCST_CONGEST_LVL>여유</FCST_CONGEST_LVL>, <FCST_CONGEST_LVL>여유</FCST_CONGEST_LVL>, <FCST_CONGEST_LVL>여유</FCST_CONGEST_LVL>, <FCST_CONGEST_LVL>여유</FCST_CONGEST_LVL>, <FCST_CONGEST_LVL>여유</FCST_CONGEST_LVL>, <FCST_CONGEST_LVL>여유</FCST_CONGEST_LVL>]
12
[]
0


In [ ]:
fcst_person_many = soup.find_all('FCST_TIME') # 12시간 예측

for i in fcst_person_many:
    parent = i.parent
    print(parent)
    print(i)


print(len(fcst_person_many))

<FCST_PPLTN><FCST_TIME>2025-03-25 00:00</FCST_TIME><FCST_CONGEST_LVL>여유</FCST_CONGEST_LVL><FCST_PPLTN_MIN>7500</FCST_PPLTN_MIN><FCST_PPLTN_MAX>8000</FCST_PPLTN_MAX></FCST_PPLTN>
<FCST_TIME>2025-03-25 00:00</FCST_TIME>
<FCST_PPLTN><FCST_TIME>2025-03-25 01:00</FCST_TIME><FCST_CONGEST_LVL>여유</FCST_CONGEST_LVL><FCST_PPLTN_MIN>6000</FCST_PPLTN_MIN><FCST_PPLTN_MAX>6500</FCST_PPLTN_MAX></FCST_PPLTN>
<FCST_TIME>2025-03-25 01:00</FCST_TIME>
<FCST_PPLTN><FCST_TIME>2025-03-25 02:00</FCST_TIME><FCST_CONGEST_LVL>여유</FCST_CONGEST_LVL><FCST_PPLTN_MIN>5000</FCST_PPLTN_MIN><FCST_PPLTN_MAX>5500</FCST_PPLTN_MAX></FCST_PPLTN>
<FCST_TIME>2025-03-25 02:00</FCST_TIME>
<FCST_PPLTN><FCST_TIME>2025-03-25 03:00</FCST_TIME><FCST_CONGEST_LVL>여유</FCST_CONGEST_LVL><FCST_PPLTN_MIN>4500</FCST_PPLTN_MIN><FCST_PPLTN_MAX>5000</FCST_PPLTN_MAX></FCST_PPLTN>
<FCST_TIME>2025-03-25 03:00</FCST_TIME>
<FCST_PPLTN><FCST_TIME>2025-03-25 04:00</FCST_TIME><FCST_CONGEST_LVL>여유</FCST_CONGEST_LVL><FCST_PPLTN_MIN>4500</FCST_PPLTN_MIN><

### 3.합쳐보기

In [ ]:

## 서울시 실시간 데이터 가져오기

#데이트 날씨 점수 = 강수점수(30) + 기온점수(20) + 대기질점수(15) + 하늘상태점수(15) 

#### 가져올 값
#핫스팟 장소명(LIVE_PPLTN_STTS), 

#### 날씨 정보
#기온(TEMP), 강수(PRECIPITATION),강수확률(RAIN_CHANCE), 강수형태(PRECPT_TYPE), 대기질(AIR_IDX), 하늘상태(SKY_STTS), 습도(HUMIDITY), 자외선(UV_INDEX)

#### 혼잡도 정보
#장소 혼잡도 지표(AREA_CONGEST_LVL), 실시간 상권현황 (LIVE_CMRCL_STTS),  장소 예측 혼잡도 지표 (FCST_CONGEST_LVL), 장소 실시간 상권 현황(AREA_CMRCL_LVL)

##불쾌지수 = 1.8 x 기온 – 0.55 x (1 – 습도) x (1.8 x 기온 – 26) + 32

구해야할 값
구, 명소명  최대 인구 , 최소 인구   기온(TEMP), 강수(PRECIPITATION),강수확률(RAIN_CHANCE), 강수형태(PRECPT_TYPE), 대기질(AIR_IDX), 하늘상태(SKY_STTS), 습도(HUMIDITY), 풍향(WIND_SPD),

In [ ]:
##### API 가져와보기
import requests
import pandas as pd 
import json
from urllib.parse import quote
from bs4 import BeautifulSoup

# 서울 지역 116곳 번호 뽑기
total_list = []
not_addr_list = []
for i in range(1,117):
    area_list = []
    #지역 코드 값 자동 완성
    area = f"POI{i:03d}"
    # API 키
    api_key = '6e51654f776b353335387168745664'
    # API URL 구성
    url = f'http://openapi.seoul.go.kr:8088/{api_key}/xml/citydata/1/2/{area}'
    # API 요청, 응답
    response = requests.get(url)
    xml_data = response.text
    # xml파싱
    soup = BeautifulSoup(xml_data, 'lxml-xml')


    
    # 특정 요소 내의 모든 항목 찾기
    live_ppltn = soup.find('LIVE_PPLTN_STTS')
    #지역
    area_nm = live_ppltn.find('AREA_NM').text
    area_list.append(area_nm)
    #혼잡도
    try:
        #구
        address = soup.find('ADDRESS').text
        gu = address.split(" ")[0]
        area_list.append(gu)

    except:
        area_list.append("주소가 안찾아짐")
    #혼잡도
    total_list.append(area_list)
    print(area_list)
   

['강남 MICE 관광특구', '강남구 삼성동 159-0', '강남구']
['동대문 관광특구', '중구 을지로7가 2-36', '중구']
['명동 관광특구', '중구 소공동 87-3 0', '중구']
['이태원 관광특구', '용산구 이태원동 127-36', '용산구']
['잠실 관광특구', '송파구 잠실동 40-1', '송파구']
['종로·청계 관광특구', '종로구 종로5가 398-3', '종로구']
['홍대 관광특구', '마포구 동교동 162-4', '마포구']
['경복궁', '종로구 내자동 35-0 내자동 54(치과의원) ~ 필운동 227(금고 앞)', '종로구']
['광화문·덕수궁', '중구 정동 5-5 (정동 5-5(시청역 2번 출구 앞)', '중구']
['보신각', '종로구 청진동 70-0', '종로구']
['서울 암사동 유적', '강동구 암사동 139-2', '강동구']
['창덕궁·종묘', '종로구 와룡동 206-0', '종로구']
['가산디지털단지역', '금천구 가산동 371-28', '금천구']
['강남역', '서초구 서초동 1330-0', '서초구']
['건대입구역', '광진구 자양동 5-5', '광진구']
['고덕역', '강동구 명일동 48-3', '강동구']
['고속터미널역', '서초구 반포동 118-3', '서초구']
['교대역', '서초구 서초동 1674-4', '서초구']
['구로디지털단지역', '구로구 구로동 1124-49', '구로구']
['구로역', '구로구 구로동 586-5', '구로구']
['군자역', '광진구 중곡동 649-4', '광진구']
['남구로역', '구로구 구로동 806-73', '구로구']
['대림역', '영등포구 대림동 808-24', '영등포구']
['동대문역', '종로구 종로6가 289-49', '종로구']
['뚝섬역', '성동구 성수동1가 656-75', '성동구']
['미아사거리역', '강북구 미아동 60-11', '강북구']
['발산역', '강서구 마곡동 797-0', '강서구']
['북한산우이역', 

In [ ]:
### 주소값이 없는애들이 있다. 구글에 검색하여 구를 가져와보자

In [418]:
not_addr_list = []
for item in total_list:
    if '주소가 안찾아짐' in item:
        not_addr_list.append(item[0].split("·")[0])

In [419]:
not_addr_list

['낙산공원', '고척돔', '서리풀공원', '서울대공원', '아차산', '청계산', '청와대']

In [ ]:
from selenium import webdriver
from selenium.webdriver.common.by import By
from bs4 import BeautifulSoup
from selenium.webdriver.chrome.service import Service
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
import urllib.parse
import re


# chrome드라이버 설정
options = webdriver.ChromeOptions()
options.add_argument('user-agent=Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/58.0.3029.110 Safari/537.3')
options.add_argument('window-size=1380,900')
driver = webdriver.Chrome(options=options)

# 좌측 검색창 이동
def switch_left():
    driver.switch_to.default_content()
    iframe = driver.find_element(By.XPATH, '//*[@id="searchIframe"]')
    driver.switch_to.frame(iframe)

# 네이버 검색
search_url = f"https://map.naver.com/p/search/{urllib.parse.quote(not_addr_name)}"


#검색창 보일때까지 기다리기
element = WebDriverWait(driver, 5).until(EC.presence_of_element_located(By.ID, "home_search_input_box"))


"input_search1742982766098"

SyntaxError: invalid syntax (4233349217.py, line 27)